Initialization

In [19]:
import math
import json
import os
import random
from IPython import display
import sympy as sp
import numpy as np
import pandas as pd
import sklearn


GREEN = "\033[92m"
RED = "\033[91m"
YELLOW = "\033[93m"
BLUE = "\033[94m"
CYAN = "\033[96m"
MAGENTA = "\033[95m"
BOLD = "\033[1m"
UNDERLINE = "\033[4m"
STANDARD = "\033[0m"

%run config.py

In [20]:
def csv2sequence(csvFile,seqFile,pref):
	with open(csvFile, 'r') as f:
		lines = f.readlines()
		with open(seqFile, 'w') as g:
			for line in lines:
				for token in line.split(','):
					if token.startswith(pref):
						token = token[len(pref):]
					token = token.strip()
					if token!="" and token!='\n':
						g.write(token+'\n')

def sequence2csv(seqFile,csvFile,dataWidth,pref):
	with open(seqFile, 'r') as f:
		lines = f.readlines()
		dataW = dataWidth
		with open(csvFile, 'w') as g:
			for line in lines:
				g.write(pref+line.strip())
				dataW -= 1
				if dataW==0:
					g.write('\n')
					dataW = dataWidth
				else:
					g.write(',')

Create the expression using flexpytester and create inputs and outputs for the test cases.

In [21]:
def generate():
	! flexpytester --generate -e symbols -s generated.py -i inputs.csv -o outputs.csv --prefix --config decayFactor=3 > /dev/null 
	! make clean > /dev/null
	! make show > /dev/null
	csv2sequence('inputs.csv','inputs.seq',"0f")
	csv2sequence('outputs.csv','outputs.seq',"0f")
	# sequence2csv('inputs.seq','prova',4,"0f")
# generate()
# display.Image("bondmachine.png")

In [22]:
# exec(open("generated.py").read())
# import IPython.display as disp
# disp.display(spExpr)

Eventually run the simbatch simulation

In [23]:
def simbatch():
	! make simbatch > /dev/null
# simbatch()

Eventually run the simulation in the FPGA with the BM

In [24]:
def bmsim():
	! make deploycollect > /dev/null
	! mv working_dir/bmsim_outputs.seq bmsim_outputs.seq
	! bondmachine -bondmachine-file working_dir/bondmachine.json -list-outputs | wc -l > num_outputs.txt
	# Read the number of outputs
	with open('num_outputs.txt','r') as f:
		num_outputs = int(f.read())
	sequence2csv('bmsim_outputs.seq','bmsim_outputs.csv',num_outputs,"")

Eventually run the simulation in the FPGA with the HLS technology

In [25]:
def hlsim():
	print ("hlsim")

Analyze the results of the chosen cases

In [26]:
def analyze():
	# Load the target outputs from the output.csv file
	targetData = np.loadtxt('outputs.csv', delimiter=',')
	simbatchData = np.loadtxt('simbatch_outputs.csv', delimiter=',')
	# bmsimData = np.loadtxt('bmsim_outputs.csv', delimiter=',')
	simbatchMSE=sklearn.metrics.mean_squared_error(targetData, simbatchData)
	# bmsimMSE=sklearn.metrics.mean_squared_error(targetData, bmsimData)

	data = {
		#"Dataset": ["Sympy target", "Simbatch", "BondMachine"],
		#"MSE" : [0.0, simbatchMSE, bmsimMSE]
		"Dataset": ["Sympy target", "Simbatch"],
		"MSE" : [0.0, simbatchMSE]
	}
	df = pd.DataFrame(data)
	return df.style.hide(axis="index")

	

Main test loop

In [27]:
# for i in range(numiterations):
# print ("Iteration: ", i)
generate()
simbatch()
# bmsim()
# hlsim()
analyze()

In [28]:
display.Image("bondmachine.png")

In [29]:
exec(open("generated.py").read())
import IPython.display as disp
disp.display(spExpr)

Matrix([
[                                                                         (y - 7.73460186110743) - 16.0941581755987, (x + y) + ((x + ((y + ((z + 11.0251421056649) - 2.30836606860339)) + 8.48858872483266)) - 6.03698690224254),                                                         (z - 6.4630686787158) + (z + (((y + (z + z)) - 2.12824039569575) - 2.5730065399626)), (x + (((y + z) - 8.97679036698405) - 12.1684839319126)) + (z - 7.10260331006806)],
[(z + ((y + (x + 0.0107045568151527)) + (z + 1.14174726141482))) + ((y - 2.11197926226029) + (z - 6.5847754999726)), (y - 9.05391271080397) + ((z + (((x + (x + z)) - 9.08670132579651) - 16.5873254638511)) + 8.06914193102673), (y + ((y - 1.83892535326705) - 5.71600065733486)) + ((y + (y + (x + ((y + (z + 1.37863690706281)) - 5.45871725768738)))) + 6.04384253424273),         (z + 7.64197216667015) + ((x + (x - 7.820958585929)) - 5.34263078532817)]])